# Lien vers le dataset : 
https://www.kaggle.com/datasets/AnalyzeBoston/crimes-in-boston

# Importation et lecture

In [20]:
import pandas as pd
import plotly.express as px
import ipywidgets as widgets
from IPython.display import display, clear_output


df = pd.read_csv('crime.csv', encoding='latin-1')

# Consultation

In [21]:
df.head()

INCIDENT_NUMBER  OFFENSE_CODE    OFFENSE_CODE_GROUP   OFFENSE_DESCRIPTION  \
0      I182070945           619               Larceny    LARCENY ALL OTHERS   
1      I182070943          1402             Vandalism             VANDALISM   
2      I182070941          3410                 Towed   TOWED MOTOR VEHICLE   
3      I182070940          3114  Investigate Property  INVESTIGATE PROPERTY   
4      I182070938          3114  Investigate Property  INVESTIGATE PROPERTY   

  DISTRICT REPORTING_AREA SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH  \
0      D14            808      NaN  2018-09-02 13:00:00  2018      9   
1      C11            347      NaN  2018-08-21 00:00:00  2018      8   
2       D4            151      NaN  2018-09-03 19:27:00  2018      9   
3       D4            272      NaN  2018-09-03 21:16:00  2018      9   
4       B3            421      NaN  2018-09-03 21:05:00  2018      9   

  DAY_OF_WEEK  HOUR    UCR_PART       STREET        Lat       Long  \
0      Sunday    13    Part One   LINCOLN ST  42.357791 -71.139371   
1     Tuesday     0    Part Two     HECLA ST  42.306821 -71.060300   
2      Monday    19  Part Three  CAZENOVE ST  42.346589 -71.072429   
3      Monday    21  Part Three   NEWCOMB ST  42.334182 -71.078664   
4      Monday    21  Part Three     DELHI ST  42.275365 -71.090361   

                      Location  
0  (42.35779134, -71.13937053)  
1  (42.30682138, -71.06030035)  
2  (42.34658879, -71.07242943)  
3  (42.33418175, -71.07866441)  
4  (42.27536542, -71.09036101)

In [22]:
len(df)

319073

In [23]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 319073 entries, 0 to 319072
Data columns (total 17 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   INCIDENT_NUMBER      319073 non-null  object 
 1   OFFENSE_CODE         319073 non-null  int64  
 2   OFFENSE_CODE_GROUP   319073 non-null  object 
 3   OFFENSE_DESCRIPTION  319073 non-null  object 
 4   DISTRICT             317308 non-null  object 
 5   REPORTING_AREA       319073 non-null  object 
 6   SHOOTING             1019 non-null    object 
 7   OCCURRED_ON_DATE     319073 non-null  object 
 8   YEAR                 319073 non-null  int64  
 9   MONTH                319073 non-null  int64  
 10  DAY_OF_WEEK          319073 non-null  object 
 11  HOUR                 319073 non-null  int64  
 12  UCR_PART             318983 non-null  object 
 13  STREET               308202 non-null  object 
 14  Lat                  299074 non-null  float64
 15  Long             

# Nettoyage du dataframe

In [24]:
df.drop('SHOOTING', axis=1, inplace=True)
df=df.dropna()

In [25]:
df=df.sample(frac=1)
df = df[0:10000]

# Affichage de notre DATA par Lat et Lon dans une map

In [26]:
# Create the initial plot for all data
fig = px.scatter_mapbox(
    df,
    lat="Lat",
    lon="Long",
    hover_name="OFFENSE_DESCRIPTION",
    hover_data={"YEAR": True, "DAY_OF_WEEK": True},
    zoom=3,
    height=500
)
fig.update_layout(
    mapbox_style="open-street-map",
    title="Crimes Map",
    margin={"r": 0, "t": 0, "l": 0, "b": 0}
)

# Create dropdown options
year_options = [{'label': 'All Years', 'value': 'All'}] + [{'label': str(year), 'value': year} for year in df['YEAR'].unique()]
day_options = [{'label': 'All Days', 'value': 'All'}] + [{'label': day, 'value': day} for day in df['DAY_OF_WEEK'].unique()]

# Function to update the figure
def update_figure(selected_year='All', selected_day='All'):
    filtered_df = df
    if selected_year != 'All':
        filtered_df = filtered_df[filtered_df['YEAR'] == selected_year]
    if selected_day != 'All':
        filtered_df = filtered_df[filtered_df['DAY_OF_WEEK'] == selected_day]

    fig = px.scatter_mapbox(
        filtered_df,
        lat="Lat",
        lon="Long",
        hover_name="OFFENSE_DESCRIPTION",
        hover_data={"YEAR": True, "DAY_OF_WEEK": True},
        zoom=3,
        height=500
    )
    fig.update_layout(
        mapbox_style="open-street-map",
        title=f"Crimes in {selected_year}" if selected_year != 'All' else "Crimes Map",
        margin={"r": 0, "t": 0, "l": 0, "b": 0}
    )
    return fig

# Update figure initially
fig = update_figure()

# Create dropdown menus
year_dropdown = {
    'buttons': [
        {
            'label': option['label'],
            'method': 'restyle',
            'args': [
                {
                    'lat': [update_figure(option['value'], 'All')['data'][0]['lat']],
                    'lon': [update_figure(option['value'], 'All')['data'][0]['lon']],
                    'text': [update_figure(option['value'], 'All')['data'][0]['text']],
                    'customdata': [update_figure(option['value'], 'All')['data'][0]['customdata']]
                },
                {
                    'hovertemplate': "<br>".join([
                        "INCIDENT_NUMBER: %{text}",
                        "YEAR: %{customdata[0]}",
                        "DAY_OF_WEEK: %{customdata[1]}"
                    ]),
                    'title': f"Crimes in {option['label']}" if option['value'] != 'All' else "Crimes Map"
                }
            ]
        }
        for option in year_options
    ],
    'direction': 'down',
    'showactive': True,
    'x': 0.17,
    'xanchor': 'left',
    'y': 1.15,
    'yanchor': 'top'
}

day_dropdown = {
    'buttons': [
        {
            'label': option['label'],
            'method': 'restyle',
            'args': [
                {
                    'lat': [update_figure('All', option['value'])['data'][0]['lat']],
                    'lon': [update_figure('All', option['value'])['data'][0]['lon']],
                    'text': [update_figure('All', option['value'])['data'][0]['text']],
                    'customdata': [update_figure('All', option['value'])['data'][0]['customdata']]
                },
                {
                    'hovertemplate': "<br>".join([
                        "INCIDENT_NUMBER: %{text}",
                        "YEAR: %{customdata[0]}",
                        "DAY_OF_WEEK: %{customdata[1]}"
                    ]),
                    'title': f"Crimes on {option['label']}" if option['value'] != 'All' else "Crimes Map"
                }
            ]
        }
        for option in day_options
    ],
    'direction': 'down',
    'showactive': True,
    'x': 0.25,
    'xanchor': 'left',
    'y': 1.15,
    'yanchor': 'top'
}

# Update figure with dropdown menus
fig.update_layout(
    updatemenus=[year_dropdown, day_dropdown]
)

# Show the figure
fig.show()


# Affichage du data

In [27]:
columns = ['OFFENSE_DESCRIPTION','YEAR','MONTH','DAY_OF_WEEK','HOUR','STREET']
# Create dropdown widget
dropdown = widgets.Dropdown(options=columns, description='Select Column:')

# Output widget to display the plot
output = widgets.Output()

# Display widgets
display(dropdown)
display(output)

# Define plotting function
def plot_column(column):
    # Clear previous output
    with output:
        clear_output(wait=True)
        # Create plot
        fig = px.histogram(df, x=column, title=f'Distribution of {column}')
        fig.show()

# Link dropdown to plot function
widgets.interactive(plot_column, column=dropdown)

Dropdown(description='Select Column:', options=('OFFENSE_DESCRIPTION', 'YEAR', 'MONTH', 'DAY_OF_WEEK', 'HOUR',…

Output()

interactive(children=(Dropdown(description='Select Column:', options=('OFFENSE_DESCRIPTION', 'YEAR', 'MONTH', …